In [7]:
%pip install ultralytics 

Note: you may need to restart the kernel to use updated packages.


In [3]:
import os
import cv2
import numpy as np
from ultralytics import YOLO
from torchvision import models, transforms
from sklearn.cluster import KMeans
import torch
from matplotlib import pyplot as plt
from PIL import Image

In [4]:
model = YOLO("yolov8n.pt").to('cuda')

100%|██████████| 6.25M/6.25M [00:00<00:00, 10.3MB/s]


In [11]:
print(model.device)

cuda:0


In [175]:
im = Image.open("dataset/1818949000-IMG-20240118-WA0001.jpg")

In [176]:
im = transforms.ToTensor()(im)
# im = im.numpy()

In [130]:
im = im.reshape(-1, im.shape[0], im.shape[1], im.shape[2])

# apply resize to image 3, 640, 640


In [161]:
im.shape

(1599, 899, 3)

In [116]:
def resize_and_pad_image(im, stride=32):
    # Get original dimensions
    _, _, h, w = im.shape

    # Calculate the nearest divisible dimensions
    new_h = int(np.ceil(h / stride) * stride)
    new_w = int(np.ceil(w / stride) * stride)

    # Resize the image while maintaining aspect ratio
    resize_transform = transforms.Compose([
        transforms.ToPILImage(),
        transforms.Resize((new_h, new_w)),  # Resize to divisible dimensions
        transforms.ToTensor()
    ])

    # Apply transform to the tensor
    im_resized = resize_transform(im.squeeze(0))  # Remove batch dimension for processing

    # Add batch dimension back
    im_resized = im_resized.unsqueeze(0)
    return im_resized

In [117]:
im = resize_and_pad_image(im)

In [177]:
im = im.numpy()

In [180]:
im.shape

(1599, 899, 3)

In [179]:
im = im.transpose(1,2,0)

In [181]:
model.eval()

YOLO(
  (model): DetectionModel(
    (model): Sequential(
      (0): Conv(
        (conv): Conv2d(3, 16, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
        (act): SiLU(inplace=True)
      )
      (1): Conv(
        (conv): Conv2d(16, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
        (act): SiLU(inplace=True)
      )
      (2): C2f(
        (cv1): Conv(
          (conv): Conv2d(32, 32, kernel_size=(1, 1), stride=(1, 1))
          (act): SiLU(inplace=True)
        )
        (cv2): Conv(
          (conv): Conv2d(48, 32, kernel_size=(1, 1), stride=(1, 1))
          (act): SiLU(inplace=True)
        )
        (m): ModuleList(
          (0): Bottleneck(
            (cv1): Conv(
              (conv): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
              (act): SiLU(inplace=True)
            )
            (cv2): Conv(
              (conv): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
              (act): SiLU(inplace=True)
   

In [182]:
with torch.no_grad():
    pred = model(im)


0: 640x384 (no detections), 40.5ms
Speed: 21.0ms preprocess, 40.5ms inference, 2.0ms postprocess per image at shape (1, 3, 640, 384)


In [196]:
for result in pred:
    boxes = result.boxes  # Boxes object for bounding box outputs
    masks = result.masks  # Masks object for segmentation masks outputs
    keypoints = result.keypoints  # Keypoints object for pose outputs
    probs = result.probs  # Probs object for classification outputs
    obb = result.obb  # Oriented boxes object for OBB outputs
    result.show()  # display to screen
    result.save(filename="result.jpg")  # save to disk

AttributeError: 'Results' object has no attribute 'ascontiguousarray'. See valid attributes below.

    A class for storing and manipulating inference results.

    This class encapsulates the functionality for handling detection, segmentation, pose estimation,
    and classification results from YOLO models.

    Attributes:
        orig_img (numpy.ndarray): Original image as a numpy array.
        orig_shape (Tuple[int, int]): Original image shape in (height, width) format.
        boxes (Boxes | None): Object containing detection bounding boxes.
        masks (Masks | None): Object containing detection masks.
        probs (Probs | None): Object containing class probabilities for classification tasks.
        keypoints (Keypoints | None): Object containing detected keypoints for each object.
        obb (OBB | None): Object containing oriented bounding boxes.
        speed (Dict[str, float | None]): Dictionary of preprocess, inference, and postprocess speeds.
        names (Dict[int

In [194]:
pred[0].boxes.xyxy

tensor([], device='cuda:0', size=(0, 4))